In [ ]:
pip install deep-pipe

In [ ]:
pip install tqdm

In [ ]:
import pickle
import torch
import torch.nn as nn
import torch.nn.functional as F
import numpy as np
from torch.utils.data import Dataset
from dpipe.layers.resblock import ResBlock2d
from dpipe.layers.conv import PreActivation2d
import copy
import matplotlib.pyplot as plt
from statistics import mean
torch.autograd.set_detect_anomaly(True)
from tqdm import tqdm_notebook as tqdm
from statistics import mean 
import os
import random
import numpy as np
from nibabel.testing import data_path
import nibabel as nib
import matplotlib.pyplot as plt
from pathlib import Path
import string
from sklearn.preprocessing import MinMaxScaler
import torch
import nibabel as nib
from torch.utils.data import Dataset
from torch.utils.data import random_split
import numpy as np
import os
from sklearn.preprocessing import MinMaxScaler
import warnings
warnings.filterwarnings('ignore')

torch.backends.cudnn.deterministic = True
random.seed(hash("setting random seeds") % 2**32 - 1)
np.random.seed(hash("improves reproducibility") % 2**32 - 1)
torch.manual_seed(hash("by removing stochasticity") % 2**32 - 1)
torch.cuda.manual_seed_all(hash("so runs are repeatable") % 2**32 - 1)

device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
print(device)

from google.colab import drive
drive.mount('/content/gdrive') #, force_remount = True

!cp -r /content/gdrive/MyDrive/VMIA_Lab_Data/surface_distance/ .
import surface_distance.surface_distance.metrics as surf_dst

cpu
Mounted at /content/gdrive


# Models

## UNet

In [ ]:
class UNet2D(nn.Module):
    def __init__(self, n_chans_in, n_chans_out, kernel_size=3, padding=1, pooling_size=2, n_filters_init=8,
                 dropout=False, p=0.1):
        super().__init__()
        self.kernel_size = kernel_size
        self.padding = padding
        self.pooling_size = pooling_size
        n = n_filters_init
        if dropout:
            dropout_layer = nn.Dropout(p)
        else:
            dropout_layer = nn.Identity()

        self.init_path = nn.Sequential(
            nn.Conv2d(n_chans_in, n, self.kernel_size, padding=self.padding, bias=False),
            nn.ReLU(),
            ResBlock2d(n, n, kernel_size=self.kernel_size, padding=self.padding),
            ResBlock2d(n, n, kernel_size=self.kernel_size, padding=self.padding),
            ResBlock2d(n, n, kernel_size=self.kernel_size, padding=self.padding)
        )
        self.shortcut0 = nn.Conv2d(n, n, 1)

        self.down1 = nn.Sequential(
            nn.BatchNorm2d(n),
            nn.Conv2d(n, n * 2, kernel_size=pooling_size, stride=pooling_size, bias=False),
            nn.ReLU(),
            dropout_layer,
            ResBlock2d(n * 2, n * 2, kernel_size=self.kernel_size, padding=self.padding),
            ResBlock2d(n * 2, n * 2, kernel_size=self.kernel_size, padding=self.padding),
            ResBlock2d(n * 2, n * 2, kernel_size=self.kernel_size, padding=self.padding)
        )
        self.shortcut1 = nn.Conv2d(n * 2, n * 2, 1)

        self.down2 = nn.Sequential(
            nn.BatchNorm2d(n * 2),
            nn.Conv2d(n * 2, n * 4, kernel_size=pooling_size, stride=pooling_size, bias=False),
            nn.ReLU(),
            dropout_layer,
            ResBlock2d(n * 4, n * 4, kernel_size=self.kernel_size, padding=self.padding),
            ResBlock2d(n * 4, n * 4, kernel_size=self.kernel_size, padding=self.padding),
            ResBlock2d(n * 4, n * 4, kernel_size=self.kernel_size, padding=self.padding)
        )
        self.shortcut2 = nn.Conv2d(n * 4, n * 4, 1)

        self.down3 = nn.Sequential(
            nn.BatchNorm2d(n * 4),
            nn.Conv2d(n * 4, n * 8, kernel_size=pooling_size, stride=pooling_size, bias=False),
            nn.ReLU(),
            dropout_layer,
            ResBlock2d(n * 8, n * 8, kernel_size=self.kernel_size, padding=self.padding),
            ResBlock2d(n * 8, n * 8, kernel_size=self.kernel_size, padding=self.padding),
            ResBlock2d(n * 8, n * 8, kernel_size=self.kernel_size, padding=self.padding),
            dropout_layer
        )

        self.up3 = nn.Sequential(
            ResBlock2d(n * 8, n * 8, kernel_size=self.kernel_size, padding=self.padding),
            ResBlock2d(n * 8, n * 8, kernel_size=self.kernel_size, padding=self.padding),
            ResBlock2d(n * 8, n * 8, kernel_size=self.kernel_size, padding=self.padding),
            nn.BatchNorm2d(n * 8),
            nn.ConvTranspose2d(n * 8, n * 4, kernel_size=self.pooling_size, stride=self.pooling_size, bias=False),
            nn.ReLU(),
            dropout_layer
        )

        self.up2 = nn.Sequential(
            ResBlock2d(n * 4, n * 4, kernel_size=self.kernel_size, padding=self.padding),
            ResBlock2d(n * 4, n * 4, kernel_size=self.kernel_size, padding=self.padding),
            ResBlock2d(n * 4, n * 4, kernel_size=self.kernel_size, padding=self.padding),
            nn.BatchNorm2d(n * 4),
            nn.ConvTranspose2d(n * 4, n * 2, kernel_size=self.pooling_size, stride=self.pooling_size, bias=False),
            nn.ReLU(),
            dropout_layer
        )

        self.up1 = nn.Sequential(
            ResBlock2d(n * 2, n * 2, kernel_size=self.kernel_size, padding=self.padding),
            ResBlock2d(n * 2, n * 2, kernel_size=self.kernel_size, padding=self.padding),
            ResBlock2d(n * 2, n * 2, kernel_size=self.kernel_size, padding=self.padding),
            nn.BatchNorm2d(n * 2),
            nn.ConvTranspose2d(n * 2, n, kernel_size=self.pooling_size, stride=self.pooling_size, bias=False),
            nn.ReLU(),
            dropout_layer
        )

        self.out_path = nn.Sequential(
            ResBlock2d(n, n, kernel_size=1),
            PreActivation2d(n, n_chans_out, kernel_size=1),
            nn.BatchNorm2d(n_chans_out)
        )

    def forward(self, x):
        x0 = self.init_path(x)
        x1 = self.down1(x0)
        x2 = self.down2(x1)
        x3 = self.down3(x2)

        x2_up = self.up3(x3)
        x1_up = self.up2(x2_up + self.shortcut2(x2))
        x0_up = self.up1(x1_up + self.shortcut1(x1))
        x_out = self.out_path(x0_up + self.shortcut0(x0))

        return F.sigmoid(x_out), x3

## Disc

In [ ]:
class Disc_Feature(nn.Module):
  def __init__(self, kernel_size=3, n_filters_init=8):
      super(Disc_Feature, self).__init__()
      n = n_filters_init

      self.conv = nn.Sequential(
          nn.Conv2d(n * 8, n * 16, stride=2, kernel_size=3),
          nn.BatchNorm2d(n*16),
          nn.ReLU(),
          nn.Conv2d(n * 16, n * 32, stride=2, kernel_size=3),
          nn.BatchNorm2d(n*32),
          nn.ReLU(),
          nn.Conv2d(n * 32, n * 64, stride=2, kernel_size=3),
          nn.BatchNorm2d(n*64),
          nn.ReLU(),
          nn.Dropout(0.25)
      )

      self.flat_map_dim = self.dummy_forward()
      
      self.fc = nn.Sequential(
      nn.Linear(self.flat_map_dim, 64),
      nn.BatchNorm1d(64),
      nn.ReLU(),
      nn.Dropout(0.5),
      nn.Linear(64, 1)
      )

      self.sigmoid = nn.Sigmoid()

  def dummy_forward(self):
      dummy_x = torch.rand(1, 64, 36, 36)
      feature_map= self.conv(dummy_x)
      flat_map_dim = feature_map.view(1, -1).shape[-1]
      return flat_map_dim

  def forward(self, x):

      feature_map = self.conv(x)
      
      batch_size = feature_map.shape[0]

      out = self.fc(feature_map.view(batch_size,-1))

      return self.sigmoid(out)

x = torch.rand(8, 64, 36, 36)
model = Disc_Feature()
print(model(x))
print(model(x).shape)

class Disc_Entropy(nn.Module):
  def __init__(self, kernel_size = 3, n_filters_init = 1):
    super(Disc_Entropy, self).__init__()
    n = n_filters_init

    self.conv = nn.Sequential(
        nn.Conv2d( 1 , 32, stride=2, kernel_size=3),
        #nn.BatchNorm2d(32),
        nn.ReLU(),
        nn.Conv2d( 32, 64 , stride=2, kernel_size=3),
        #nn.BatchNorm2d(64),
        nn.ReLU(),
        nn.Conv2d( 64, 128, stride=2, kernel_size=3),
        #nn.BatchNorm2d(128),
        nn.ReLU(),
        nn.Conv2d(128, 256, stride=2, kernel_size=3),
        #nn.BatchNorm2d( 256),
        nn.ReLU(),
        nn.Conv2d(256, 512, stride=2, kernel_size=3),
        #nn.BatchNorm2d( 512),
        nn.ReLU(),
        #nn.Dropout(0.25)
    )

    self.flat_map_dim = 512*8*8 

    self.fc = nn.Sequential(
        nn.Linear(self.flat_map_dim, 512),
        #nn.BatchNorm1d(512),
        nn.ReLU(),
        nn.Linear(512, 64),
        #nn.BatchNorm1d(64),
        nn.ReLU(),
        nn.Linear(64, 1)
        #nn.Dropout(0.5),    
    )

    self.sigmoid = nn.Sigmoid()
   

  def forward(self, x):

    x1 = self.conv(x) # (B, 512, 8, 8)

    batch_size = x1.shape[0]
    
    x2 = self.fc( x1.view(batch_size,-1) )
  
    return self.sigmoid(x2)

x = torch.rand(8, 1, 288, 288)
model = Disc_Entropy()
print(model(x))
print(model(x).shape)

tensor([[0.4604],
        [0.4894],
        [0.3571],
        [0.4472],
        [0.5385],
        [0.4879],
        [0.4768],
        [0.6699]], grad_fn=<SigmoidBackward0>)
torch.Size([8, 1])
tensor([[0.4758],
        [0.4760],
        [0.4758],
        [0.4759],
        [0.4759],
        [0.4759],
        [0.4758],
        [0.4759]], grad_fn=<SigmoidBackward0>)
torch.Size([8, 1])


# Load dict

In [ ]:
base_path = '/content/gdrive/MyDrive/VMIA_Lab_Data/data/'

with open(base_path + 'vol_split_dict.pkl', 'rb') as handle:
  volume_path_dict = pickle.load(handle)

In [ ]:
volume_path_dict

{'ge_15_test': ['CC0293_ge_15_50_M.nii.gz',
  'CC0294_ge_15_51_M.nii.gz',
  'CC0295_ge_15_55_M.nii.gz',
  'CC0296_ge_15_57_F.nii.gz',
  'CC0297_ge_15_57_F.nii.gz',
  'CC0298_ge_15_58_M.nii.gz',
  'CC0299_ge_15_37_M.nii.gz'],
 'ge_15_train': ['CC0240_ge_15_60_F.nii.gz',
  'CC0241_ge_15_60_F.nii.gz',
  'CC0242_ge_15_55_F.nii.gz',
  'CC0243_ge_15_58_F.nii.gz',
  'CC0244_ge_15_56_F.nii.gz',
  'CC0245_ge_15_48_M.nii.gz',
  'CC0246_ge_15_60_F.nii.gz',
  'CC0247_ge_15_53_M.nii.gz',
  'CC0248_ge_15_51_M.nii.gz',
  'CC0249_ge_15_58_F.nii.gz',
  'CC0250_ge_15_60_F.nii.gz',
  'CC0251_ge_15_41_M.nii.gz',
  'CC0252_ge_15_44_M.nii.gz',
  'CC0253_ge_15_58_M.nii.gz',
  'CC0254_ge_15_57_F.nii.gz',
  'CC0255_ge_15_57_F.nii.gz',
  'CC0256_ge_15_42_M.nii.gz',
  'CC0257_ge_15_57_F.nii.gz',
  'CC0258_ge_15_55_F.nii.gz',
  'CC0259_ge_15_56_F.nii.gz',
  'CC0260_ge_15_51_M.nii.gz',
  'CC0261_ge_15_59_F.nii.gz',
  'CC0262_ge_15_54_M.nii.gz',
  'CC0263_ge_15_51_M.nii.gz',
  'CC0264_ge_15_59_F.nii.gz',
  'CC0265_

# Score Functions:

In [ ]:
def process_image(img, max_pad = 288):
     
    '''
    MIN-MAX SCALE THE IMAGE
    '''
    assert (len(img.shape) == 3)
    assert img.min() == 0
    img = img/img.max()
    
    '''
    FIND NON UNIQUE AXIS AND BRING TO 0-TH POS
    '''
    vals, counts = np.unique(img.shape, return_counts = True)
    
    no_of_scans = vals[counts == 1]
    image_size = vals[counts == 2]
    
    assert (len(no_of_scans) == 1) and (len(image_size) == 1)
    img = np.swapaxes( img, 0, np.where(img.shape == no_of_scans)[0][0] )
    
    '''
    PAD IMAGE TO MAX SIZE
    '''
    pad_size = int((max_pad - image_size[0])/2)   
    
    
    return np.pad(img, pad_width = ((0, 0), (pad_size, pad_size), (pad_size, pad_size)), mode =  'constant', constant_values = 0)



In [ ]:
@torch.no_grad()
def Volumetric_Dice_Score(path, filename, segmenter):

    device = torch.device("cuda" if torch.cuda.is_available() else "cpu")

    # READ IMG AND GET PREDS
    #img = nib.load(path + 'Original/' + filename).get_fdata()
    segmenter.eval()

    img = process_image(nib.load(path + 'Original/' + filename).get_fdata())
    

    batch_size = 1
    out,_ = segmenter(torch.from_numpy( img[0:0 + batch_size,:,:]).unsqueeze(dim = 1).float().to(device))
    start_idx = batch_size

    for i in tqdm(range( int(img.shape[0]/batch_size) - 1)):
      out1,_ = segmenter(torch.from_numpy( img[start_idx: start_idx+ batch_size,:,:]).unsqueeze(dim = 1).float().to(device))
      out = torch.cat([out, out1], dim = 0)
      start_idx += batch_size
    
    pred = torch.where(out > 0.5, 1, 0)

    # READ MASK 
    mask_filename = filename.split(".nii")[0] + "_ss.nii.gz"
    mask = process_image(nib.load(path + 'Silver-standard/' + mask_filename).get_fdata())

    mask_bool = mask.astype(bool)
    pred_bool = pred.squeeze().detach().to('cpu').numpy().astype(bool)

    assert img.shape == mask.shape == mask_bool.shape == pred_bool.shape
    print("shapes: ",img.shape)

    # GET SCORE
    score = surf_dst.compute_dice_coefficient( mask_bool, pred_bool)

    sds = surf_dst.compute_surface_distances( mask_bool, pred_bool, [1,1,1])
    asd = surf_dst.compute_average_surface_distance(sds)
    sdat = surf_dst.compute_surface_dice_at_tolerance(sds, 1)    
    hd = surf_dst.compute_robust_hausdorff(sds, 95)

    print(filename,"Surface Dice:",score,"| SD at tol:", sdat,"| HD:", hd)

    return score, sdat, hd

@torch.no_grad()         
def Eval_Vol_Dice(domain, scan_type, mode, segmenter, val_stats, curr_epoch):

    dice_scores = []
    sdat_scores = []
    hd_scores = []

    base_path = '/content/gdrive/MyDrive/VMIA_Lab_Data/data/'

    with open(base_path + 'vol_split_dict.pkl', 'rb') as handle:
      volume_path_dict = pickle.load(handle)

    file_list = volume_path_dict[str(domain) + '_' + scan_type + '_' + str(mode)]

    for filename in tqdm(file_list):
      
      score, sdat, hd = Volumetric_Dice_Score(base_path, filename, segmenter)
      dice_scores.append( score )
      sdat_scores.append( sdat )
      hd_scores.append( hd )

    
    val_stats[str(domain) + '_' + scan_type + '_' + str(mode) + '_vol_dice'] = dice_scores
    val_stats[str(domain) + '_' + scan_type + '_' + str(mode) + '_vol_sdat'] = sdat_scores
    val_stats[str(domain) + '_' + scan_type + '_' + str(mode) + '_vol_hd'] = hd_scores

    val_vol_dice = mean(dice_scores)
    val_vol_sdat = mean(sdat_scores)
    val_vol_hd = mean(hd_scores)
    
    print()
    print(domain,'vol metrics for epoch',curr_epoch)
    print('AVG VOLUMETRIC DICE :',val_vol_dice,"| SD AT TOL:", val_vol_sdat,"| HD:", val_vol_hd,'#########')


    return val_stats

# Run

In [ ]:
vol_split_stats = {}
segmenter = torch.load('/content/gdrive/MyDrive/VMIA_Lab_Data/GE3/ge3_updateddata_train70_25epochs_combinedloss.pkl', map_location=torch.device(device))

In [ ]:
dtype = ['ge', 'philips', 'siemens']
ptype = ['3','15']
modes = ['test','val','train']

for d in dtype:
    for p in ptype:
      for m in modes:
        
        print(d, " --- ", p, "---", m)
        vol_split_stats = Eval_Vol_Dice(d, p, m ,segmenter, vol_split_stats, 0)

ge  ---  3 --- test


  0%|          | 0/7 [00:00<?, ?it/s]

  0%|          | 0/171 [00:00<?, ?it/s]

shapes:  (172, 288, 288)
CC0353_ge_3_58_F.nii.gz Surface Dice: 0.9888250304018462 | SD at tol: 0.9615145013993627 | HD: 1.0


  0%|          | 0/199 [00:00<?, ?it/s]

...

shapes:  (192, 288, 288)
CC0159_siemens_15_54_M.nii.gz Surface Dice: 0.9136912413623032 | SD at tol: 0.6280030045477819 | HD: 22.315913604421397


  0%|          | 0/191 [00:00<?, ?it/s]

shapes:  (192, 288, 288)
CC0160_siemens_15_57_F.nii.gz Surface Dice: 0.980106116306903 | SD at tol: 0.8869781440251049 | HD: 8.48528137423857


  0%|          | 0/191 [00:00<?, ?it/s]

shapes:  (192, 288, 288)
CC0161_siemens_15_55_F.nii.gz Surface Dice: 0.9685990149831716 | SD at tol: 0.8419665453935561 | HD: 14.352700094407323

siemens vol metrics for epoch 0
AVG VOLUMETRIC DICE : 0.9568719955200279 | SD AT TOL: 0.7951701549829168 | HD: 15.726841191862295 #########


In [ ]:
vol_split_stats

{'ge_15_test_vol_dice': [0.9473338838936207,
  0.7759842624530057,
  0.8036599366368985,
  0.9147576821718133,
  0.8546357397403198,
  0.8672805827969647,
  0.9388728825875813],
 'ge_15_test_vol_hd': [12.36931687685298,
  28.948229652260256,
  25.059928172283335,
  18.627936010197157,
  27.27636339397171,
  19.05255888325765,
  15.84297951775486],
 'ge_15_test_vol_sdat': [0.7229810783154513,
  0.39998190800769406,
  0.4556255754857146,
  0.6698261873211145,
  0.5318647305944896,
  0.6087333102315684,
  0.6701982349242351],
 'ge_15_train_vol_dice': [0.9661187200051021,
  0.8427926013157042,
  0.9188156455837847,
  0.9210992322079506,
  0.7773835358522809,
  0.9530385535033818,
  0.9059374485209328,
  0.9128587280333288,
  0.8117927397082723,
  0.8076502601899446,
  0.8612123219609142,
  0.9006700389241216,
  0.7892125465796164,
  0.8826588569020364,
  0.7815404468984071,
  0.8349963382393052,
  0.8426657397341792,
  0.8398655237278524,
  0.9064255947213058,
  0.8706850897886477,
  0.741

In [ ]:
with open('/content/gdrive/MyDrive/VMIA_Lab_Data/data/vol_split_stats.pkl', 'wb') as handle:
    pickle.dump(vol_split_stats, handle)

# Calc Score

In [91]:
with open('/content/gdrive/MyDrive/VMIA_Lab_Data/data/vol_split_stats.pkl', 'rb') as handle:
      vol_stats = pickle.load(handle)

In [97]:
dice_scores = {}
sdat_scores = {}
hd_scores = {}

domains = ['ge','philips','siemens']
scan_types = ['3','15']
scores = ['dice','sdat','hd']

mean_stats = {}

for d in domains:
    for s in scan_types:
        for score in scores:
            print(d+s+"_"+score)
            
            if d+s not in mean_stats.keys():
                mean_stats[d+s] = {}
            
            l = []
            l.extend(vol_stats[d + "_" + s + "_train_" + 'vol_' + score])
            l.extend(vol_stats[d + "_" + s + "_val_" + 'vol_' + score])
            l.extend(vol_stats[d + "_" + s + "_test_" + 'vol_' + score])
                    
            mean_stats[d+s][score] = np.round(mean(l),2)

ge3_dice
ge3_sdat
ge3_hd
ge15_dice
ge15_sdat
ge15_hd
philips3_dice
philips3_sdat
philips3_hd
philips15_dice
philips15_sdat
philips15_hd
siemens3_dice
siemens3_sdat
siemens3_hd
siemens15_dice
siemens15_sdat
siemens15_hd


In [101]:
final_mean_stats = pd.DataFrame.from_dict(mean_stats).T

In [100]:
final_mean_stats

dice  sdat     hd
ge3        0.99  0.96   1.22
ge15       0.87  0.58  21.08
philips3   0.92  0.69  17.48
philips15  0.96  0.80  24.67
siemens3   0.98  0.87   9.98
siemens15  0.96  0.79  16.34

In [102]:
final_mean_stats.to_csv('/content/gdrive/MyDrive/VMIA_Lab_Data/data/mean_vol_stats_src_ge.csv',index=False)